In [5]:
import pandas as pd 
import datetime 
import numpy as np

In [6]:
density_reports = pd.read_excel("data/raw/DensityReports.xlsx")
product_attributes = pd.read_excel("data/raw/ProductAttributes.xlsx")
supplier_scorecard = pd.read_excel("data/raw/SupplierScorecard.xlsx")
historical_incidents = pd.read_excel("data/raw/HistoricalIncidents.xlsx")

# Data Cleaning Notebook – Table of Contents

This notebook covers the cleaning and standardization of all four datasets used in the packaging quality classification project.

- [Cleaning Density Reports](#Cleaning-Density-Reports)
- [Cleaning Product Attributes](#Cleaning-Product-Attributes)
- [Cleaning Supplier ScoreCard](#Cleaning-Supplier-ScoreCard)
- [Cleaning Historical Incidents](#Cleaning-Historical-Incidents)
- [Processed Data Download](#Processed-Data-Download)


### Cleaning Density Reports

Summary of Major Data Cleaning Steps for `DensityReports`

- Removed all `ProductReference` entries not found in the `ProductAttributes` dataset after confirming they referred to inconsistent product records.
- Standardized `ProductReference` values by removing trailing "X" where applicable, as they matched base product codes.
- Unified inconsistent supplier names by normalizing casing and applying a mapping to correct common variations.
- Removed rows with implausible `ProposedUnitsPerCarton` values such as -3, 0, and 9999.
- Dropped rows with missing `ProposedFoldingMethod` values and standardized the naming across valid entries.
- Standardized value formats in the `ProposedLayout` column.
- Cleaned and standardized the `PackagingQuality` column (target variable) to ensure consistent labeling.
- Resulting cleaned dataset contains 478,846 rows — a 4.23% reduction from the original 500,000 records.


In [7]:
print("density_reports columns:", density_reports.columns.tolist())
print("density_reports shape:", density_reports.shape)

density_reports columns: ['ReportID', 'ProductReference', 'DateOfReport', 'SupplierName', 'GarmentType', 'Material', 'Weight', 'ProposedUnitsPerCarton', 'ProposedFoldingMethod', 'ProposedLayout', 'PackagingQuality']
density_reports shape: (500000, 11)


In [8]:
print("product_attributes columns:", product_attributes.columns.tolist())
print("product_attributes shape:", product_attributes.shape)

product_attributes columns: ['ProductReference', 'ProductName', 'GarmentType', 'Material', 'Size', 'Collection', 'Weight']
product_attributes shape: (10000, 7)


This block checks whether all `ProductReference` values in `DensityReports` exist in `ProductAttributes`. If any are missing, it returns those unmatched references along with the number of rows they appear in within `DensityReports`.


In [9]:
# Find unique ProductReference values in each dataframe
density_refs = set(density_reports['ProductReference'].unique())
attributes_refs = set(product_attributes['ProductReference'].unique())

# Find ProductReference values in density_reports not present in product_attributes
missing_refs = density_refs - attributes_refs

# Filter only rows with missing ProductReference values once
if missing_refs:
    missing_df = density_reports[density_reports['ProductReference'].isin(missing_refs)]
    counts = missing_df['ProductReference'].value_counts()

    print("ProductReference values in density_reports not present in product_attributes:")
    for ref, count in counts.items():
        print(f"{ref}: {count} rows")
    print(f"\nTotal missing ProductReference values: {len(missing_refs)}")
else:
    print("All ProductReference values in density_reports are present in product_attributes.")


ProductReference values in density_reports not present in product_attributes:
PRD06: 793 rows
PRD00: 791 rows
PRD01: 782 rows
PRD05: 777 rows
PRD03: 768 rows
PRD02: 759 rows
PRD07: 756 rows
PRD08: 746 rows
PRD09: 746 rows
PRD04: 734 rows
PRD03174X: 5 rows
PRD07746X: 5 rows
PRD09398X: 5 rows
PRD07652X: 5 rows
PRD07381X: 5 rows
PRD07540X: 5 rows
PRD08479X: 4 rows
PRD08796X: 4 rows
PRD03428X: 4 rows
PRD08627X: 4 rows
PRD04986X: 4 rows
PRD03459X: 4 rows
PRD08098X: 4 rows
PRD08632X: 4 rows
PRD08620X: 4 rows
PRD05079X: 4 rows
PRD06347X: 4 rows
PRD08016X: 4 rows
PRD03365X: 4 rows
PRD04031X: 4 rows
PRD02898X: 4 rows
PRD08599X: 4 rows
PRD06483X: 4 rows
PRD06913X: 4 rows
PRD00905X: 4 rows
PRD06434X: 4 rows
PRD00528X: 4 rows
PRD03973X: 4 rows
PRD04446X: 4 rows
PRD05048X: 4 rows
PRD07276X: 4 rows
PRD07268X: 4 rows
PRD08804X: 4 rows
PRD06863X: 4 rows
PRD05250X: 4 rows
PRD02101X: 4 rows
PRD08806X: 4 rows
PRD01899X: 4 rows
PRD01419X: 4 rows
PRD06302X: 4 rows
PRD06154X: 4 rows
PRD02938X: 4 rows
PRD032

The selected `ProductReference` values were specifically chosen because they exist in the `DensityReports` dataset but are missing from `ProductAttributes`. This code allows a quick side-by-side inspection of two example rows per reference to investigate whether they represent **unique or anomalous products** that were never logged in the official product attributes database.

This step helps you verify if:

* These entries are consistently defined across rows,
* They reflect forgotten or out-of-catalog products,
* Or if they result from data entry errors or mismatched taxonomy.


In [10]:

# Define the target ProductReference values
target_refs = ['PRD06', 'PRD00', 'PRD01', 'PRD05', 'PRD03', 
               'PRD02', 'PRD07', 'PRD08', 'PRD09', 'PRD04']

# Filter for those references
filtered_rows = density_reports[density_reports['ProductReference'].isin(target_refs)]

# Take 2 rows per ProductReference
sampled = (
    filtered_rows.groupby('ProductReference')
    .head(2)
    .assign(RowNum=lambda df: df.groupby('ProductReference').cumcount())
)

# Pivot to show row 0 and row 1 side by side
wide_format = (
    sampled
    .pivot(index='ProductReference', columns='RowNum')
    .reset_index()
)

# Flatten multi-level column names
wide_format.columns = [
    f"{col[0]}_{col[1]}" if col[1] != '' else col[0] 
    for col in wide_format.columns
]

# Display result
print(wide_format)



  ProductReference  ReportID_0  ReportID_1 DateOfReport_0 DateOfReport_1  \
0            PRD00  RPT0000753  RPT0000966     2024-01-29     2023-12-01   
1            PRD01  RPT0000844  RPT0001385     2023-11-16     2024-01-30   
2            PRD02  RPT0001439  RPT0003099     2023-12-16     2023-10-20   
3            PRD03  RPT0000740  RPT0001097     2023-08-24     2024-04-26   
4            PRD04  RPT0000974  RPT0001005     2023-05-11     2024-06-06   
5            PRD05  RPT0000122  RPT0000741     2024-06-26     2023-05-03   
6            PRD06  RPT0000978  RPT0002098     2024-03-18     2023-09-06   
7            PRD07  RPT0000295  RPT0000415     2023-05-14     2024-03-09   
8            PRD08  RPT0001615  RPT0001900     2023-07-15     2024-04-26   
9            PRD09  RPT0000211  RPT0000761     2023-09-16     2023-07-02   

  SupplierName_0 SupplierName_1 GarmentType_0 GarmentType_1 Material_0  ...  \
0      SupplierA      SupplierA         Shirt       Sweater     Cotton  ...   
1    

Upon inspection, the missing `ProductReference` values do **not correspond to a single, consistent product** each. Instead, they are linked to multiple varying entries, indicating potential data inconsistencies or placeholder codes. As a result, it is most appropriate to **drop these entries** from the analysis to maintain data integrity.


In [11]:
density_reports = density_reports[~density_reports['ProductReference'].isin(target_refs)].reset_index(drop=True)

We observed that some `ProductReference` values have counterparts ending with an "X". This likely indicates **taxonomy inconsistencies** or alternate codings for the same product. The following code compares rows **side-by-side** for references that share the same numeric base but differ by the trailing "X" to assess whether they refer to the **same underlying product** or should be treated separately.

If you’d like, I can walk through the corresponding code block that implements this logic and explain it line by line as well. Just paste it when you're ready.


In [12]:
# Define the target ProductReference values
target_refs = ['PRD03174X','PRD03174','PRD07746X','PRD07746','PRD09398X','PRD09398']

# Filter for those references
filtered_rows = density_reports[density_reports['ProductReference'].isin(target_refs)]

# Take 2 rows per ProductReference
sampled = (
    filtered_rows.groupby('ProductReference')
    .head(2)
    .assign(RowNum=lambda df: df.groupby('ProductReference').cumcount())
)

# Pivot to show row 0 and row 1 side by side
wide_format = (
    sampled
    .pivot(index='ProductReference', columns='RowNum')
    .reset_index()
)

# Flatten multi-level column names
wide_format.columns = [
    f"{col[0]}_{col[1]}" if col[1] != '' else col[0] 
    for col in wide_format.columns
]

# Keep only GarmentType, Material, and Weight columns
columns_to_keep = ['ProductReference'] + [
    col for col in wide_format.columns 
    if any(key in col for key in ['GarmentType', 'Material', 'Weight'])
]
filtered_output = wide_format[columns_to_keep]

# Display result
print(filtered_output)


  ProductReference GarmentType_0 GarmentType_1 Material_0 Material_1  \
0         PRD03174         Shirt         Shirt      Linen      Linen   
1        PRD03174X         Shirt         Shirt      Linen      Linen   
2         PRD07746         Skirt         Skirt     Cotton     Cotton   
3        PRD07746X         Skirt         Skirt     Cotton     Cotton   
4         PRD09398         Dress         Dress      Linen      Linen   
5        PRD09398X         Dress         Dress      Linen      Linen   

   Weight_0  Weight_1  
0      0.16      0.16  
1      0.16      0.16  
2      0.29      0.29  
3      0.29      0.29  
4      0.50      0.50  
5      0.50      0.50  


The comparison confirms that `ProductReference` values ending with "X" refer to the **same underlying products** as their base versions. To ensure consistency and avoid duplication during merging or modeling, we will **standardize these references by removing the trailing "X"** across the dataset.


In [13]:
# Remove the letter 'X' from ProductReference values
density_reports['ProductReference'] = density_reports['ProductReference'].str.replace('X', '', regex=False)

In [14]:
density_reports['DateOfReport'] = pd.to_datetime(density_reports['DateOfReport'])

In [15]:
unique_suppliers = density_reports['SupplierName'].unique()
print(unique_suppliers)

['SupplierA' 'SupplierC' 'SupplierD' 'SupplierB' 'supplierA' 'SupplierF'
 'SupplierE' 'supplierh' 'SupplierH' 'SuppB' 'SupplierG' 'SupllierC'
 'SPLF' 'SuplA']


As the output above displays, several suppliers appear with inconsistent or misspelled names across the datasets, often due to variations in spacing, capitalization, or typographical errors. To ensure reliable merging and analysis based on `SupplierName`, the following code standardizes these entries by converting all names a consistent, unified format.


In [16]:
# Step 1: Normalize casing (force consistent capitalization)
density_reports['SupplierName'] = density_reports['SupplierName'].str.strip().str.lower()

# Step 2: Define mapping from lower-case to standardized names
supplier_mapping = {
    'suppliera': 'SupplierA',
    'supplierb': 'SupplierB',
    'supplierc': 'SupplierC',
    'supplierd': 'SupplierD',
    'suppliere': 'SupplierE',
    'supplierf': 'SupplierF',
    'supplierg': 'SupplierG',
    'supplierh': 'SupplierH',
    'suppb': 'SupplierB',
    'supla': 'SupplierA',
    'splf': 'SupplierF',
    'supllierc': 'SupplierC'
}

# Step 3: Replace using mapping
density_reports['SupplierName'] = density_reports['SupplierName'].replace(supplier_mapping)

# Step 4: Check result
print(sorted(density_reports['SupplierName'].unique()))



['SupplierA', 'SupplierB', 'SupplierC', 'SupplierD', 'SupplierE', 'SupplierF', 'SupplierG', 'SupplierH']


In [17]:
unique_garment_types = density_reports['GarmentType'].unique()
unique_materials = density_reports['Material'].unique()
print("Unique GarmentType values:", unique_garment_types)
print("Unique Material values:", unique_materials)

Unique GarmentType values: ['Pants' 'T-Shirt' 'Shirt' 'Coat' 'Dress' 'Blouse' 'Suit' 'Hoodie' 'Skirt'
 'Jacket' 'Shorts' 'Sweater']
Unique Material values: ['Polyester' 'Denim' 'Cotton' 'Linen' 'Wool' 'Silk']


In [18]:
unique_weights = np.sort(density_reports['Weight'].unique())[::-1]
print("Unique Weight values (sorted descending):", unique_weights)

Unique Weight values (sorted descending): [2.32 2.25 2.22 2.21 2.2  2.18 2.12 2.08 2.07 2.05 2.04 2.03 2.02 2.01
 2.   1.99 1.96 1.95 1.93 1.92 1.91 1.89 1.88 1.86 1.85 1.83 1.82 1.81
 1.8  1.79 1.77 1.76 1.74 1.73 1.72 1.71 1.7  1.69 1.68 1.67 1.66 1.65
 1.64 1.63 1.62 1.61 1.6  1.59 1.58 1.57 1.56 1.55 1.54 1.53 1.52 1.51
 1.5  1.49 1.48 1.47 1.46 1.45 1.44 1.43 1.42 1.41 1.4  1.39 1.38 1.37
 1.36 1.35 1.34 1.33 1.32 1.31 1.3  1.29 1.28 1.27 1.26 1.25 1.24 1.23
 1.22 1.21 1.2  1.19 1.18 1.17 1.16 1.15 1.14 1.13 1.12 1.11 1.1  1.09
 1.08 1.07 1.06 1.05 1.04 1.03 1.02 1.01 1.   0.99 0.98 0.97 0.96 0.95
 0.94 0.93 0.92 0.91 0.9  0.89 0.88 0.87 0.86 0.85 0.84 0.83 0.82 0.81
 0.8  0.79 0.78 0.77 0.76 0.75 0.74 0.73 0.72 0.71 0.7  0.69 0.68 0.67
 0.66 0.65 0.64 0.63 0.62 0.61 0.6  0.59 0.58 0.57 0.56 0.55 0.54 0.53
 0.52 0.51 0.5  0.49 0.48 0.47 0.46 0.45 0.44 0.43 0.42 0.41 0.4  0.39
 0.38 0.37 0.36 0.35 0.34 0.33 0.32 0.31 0.3  0.29 0.28 0.27 0.26 0.25
 0.24 0.23 0.22 0.21 0.2  0.19 0.18

Since a weight of `0.08` seems implausibly low, we're investigating whether such entries might actually correspond to valid items with a different recorded weight. The code below filters and displays 10 sample rows from `density_reports` where the weight is `0.08`, allowing us to inspect whether these could plausibly match or explain the `0.08` cases.


In [19]:
# Filter 10 rows from density_reports where Weight is exactly 0.08
rows_with_weight_008 = density_reports[density_reports['Weight'] == 0.08].head(10)
print(rows_with_weight_008)

          ReportID ProductReference DateOfReport SupplierName GarmentType  \
949     RPT0000960         PRD05743   2024-02-13    SupplierE     T-Shirt   
36101   RPT0036639         PRD05743   2023-10-24    SupplierD     T-Shirt   
38909   RPT0039481         PRD05743   2024-05-05    SupplierG     T-Shirt   
52824   RPT0053593         PRD05743   2024-06-03    SupplierF     T-Shirt   
62655   RPT0063590         PRD05743   2023-01-03    SupplierC     T-Shirt   
78174   RPT0079359         PRD05743   2024-03-06    SupplierA     T-Shirt   
83744   RPT0085028         PRD05743   2023-08-02    SupplierF     T-Shirt   
89831   RPT0091206         PRD05743   2023-01-22    SupplierC     T-Shirt   
110577  RPT0112269         PRD05743   2023-11-13    SupplierE     T-Shirt   
116696  RPT0118492         PRD05743   2023-11-08    SupplierD     T-Shirt   

       Material  Weight  ProposedUnitsPerCarton ProposedFoldingMethod  \
949        Silk    0.08                    48.0               Method3   
36101 

It is definetly plausible

In [20]:
import plotly.express as px

fig = px.histogram(density_reports, x='Weight', nbins=50, title='Distribution of Weight in density_reports')
fig.show()

In [21]:
unique_units_per_carton = np.sort(density_reports['ProposedUnitsPerCarton'].unique())
print("Unique values of ProposedUnitsPerCarton:", unique_units_per_carton)

Unique values of ProposedUnitsPerCarton: [-3.000e+00  0.000e+00  4.000e+00  5.000e+00  6.000e+00  7.000e+00
  8.000e+00  9.000e+00  1.000e+01  1.100e+01  1.200e+01  1.250e+01
  1.300e+01  1.400e+01  1.500e+01  1.600e+01  1.700e+01  1.800e+01
  1.900e+01  2.000e+01  2.100e+01  2.200e+01  2.300e+01  2.400e+01
  2.500e+01  2.600e+01  2.700e+01  2.800e+01  2.900e+01  3.000e+01
  3.100e+01  3.200e+01  3.300e+01  3.400e+01  3.500e+01  3.600e+01
  3.700e+01  3.800e+01  3.900e+01  4.000e+01  4.100e+01  4.200e+01
  4.300e+01  4.400e+01  4.500e+01  4.600e+01  4.700e+01  4.800e+01
  4.900e+01  9.999e+03]


As seen in the output above, the `ProposedUnitsPerCarton` column contains implausible values such as `-3`, `0`, and `9999`. These are not realistic packaging recommendations. To assess their impact, we will first count how frequently these values occur to determine whether they are isolated anomalies or more widespread. Regardless of frequency, such values will ultimately be removed from the dataset, as they are not plausible for analysis or modeling.


In [22]:
# Count occurrences of each special value in ProposedUnitsPerCarton
special_values = [-3, 0, 9999]
counts_each = density_reports['ProposedUnitsPerCarton'].value_counts().reindex(special_values, fill_value=0)
total_special = counts_each.sum()

print("Counts for each special value in ProposedUnitsPerCarton:")
print(counts_each)
print(f"\nTotal rows with ProposedUnitsPerCarton as -3, 0, or 9999: {total_special}")

Counts for each special value in ProposedUnitsPerCarton:
ProposedUnitsPerCarton
-3       3692
 0       3646
 9999    3726
Name: count, dtype: int64

Total rows with ProposedUnitsPerCarton as -3, 0, or 9999: 11064


In [23]:
# Drop rows where ProposedUnitsPerCarton is -3, 0, or 9999
density_reports = density_reports[~density_reports['ProposedUnitsPerCarton'].isin(special_values)].reset_index(drop=True)

In [24]:
unique_folding_methods = density_reports['ProposedFoldingMethod'].unique()
print("Unique values of ProposedFoldingMethod:", unique_folding_methods)

Unique values of ProposedFoldingMethod: ['Method2' 'Method1' 'Method3' 'Method_2' nan 'Methd1' 'FoldX']


The output shows that the `ProposedFoldingMethod` column contains **inconsistent naming conventions** and **missing values** (`nulls`). To clean this column, the following code will:

1. **Count** the number of missing values,
2. **Remove** rows where the folding method is missing, and
3. **Standardize** the naming of folding methods to ensure consistency across the dataset.


In [25]:
nan_counts = density_reports.isna().sum()
print("NaN values per column in density_reports:")
print(nan_counts)

NaN values per column in density_reports:
ReportID                     0
ProductReference             0
DateOfReport                 0
SupplierName                 0
GarmentType                  0
Material                     0
Weight                       0
ProposedUnitsPerCarton       0
ProposedFoldingMethod     2438
ProposedLayout               0
PackagingQuality             0
dtype: int64


In [26]:
density_reports = density_reports.dropna().reset_index(drop=True)

In [27]:
# Step 1: Convert to string and strip whitespace
density_reports['ProposedFoldingMethod'] = density_reports['ProposedFoldingMethod'].astype(str).str.strip()
# Step 2: Define mapping
method_mapping = {
    'Methd1': 'Method1',
    'Method_2': 'Method2',
    'FoldX': 'Method4'
}

# Step 3: Replace values using the mapping
density_reports['ProposedFoldingMethod'] = density_reports['ProposedFoldingMethod'].replace(method_mapping)

# Step 4: Check cleaned unique values
print(density_reports['ProposedFoldingMethod'].unique())


['Method2' 'Method1' 'Method3' 'Method4']


In [28]:
unique_layouts = density_reports['ProposedLayout'].unique()
print("Unique values of ProposedLayout:", unique_layouts)

Unique values of ProposedLayout: ['LayoutC' 'LayoutB' 'LayoutA' 'LayoutD' 'LayoutE' 'LayoutX' 'Box9'
 'layouta' 'LayC']


The `ProposedLayout` column contains variations in layout naming that need to be standardized for consistency. 
The following code will clean and unify these values.


In [29]:
# Step 1: Convert to lowercase strings and strip spaces
density_reports['ProposedLayout'] = density_reports['ProposedLayout'].astype(str).str.strip().str.lower()

# Step 2: Define mapping (lowercase keys → desired standardized values)
layout_mapping = {
    'layouta': 'LayoutA',
    'layoutb': 'LayoutB',
    'layoutc': 'LayoutC',
    'layoutd': 'LayoutD',
    'layc': 'LayoutC',
    'layoute': 'LayoutE',
    'layoutx': 'LayoutX',
    'box9': 'LayoutF'  # or replace with another layout if needed
}

# Step 3: Replace using the mapping
density_reports['ProposedLayout'] = density_reports['ProposedLayout'].replace(layout_mapping)

# Step 4: Check cleaned unique values
print(sorted(density_reports['ProposedLayout'].unique()))


['LayoutA', 'LayoutB', 'LayoutC', 'LayoutD', 'LayoutE', 'LayoutF', 'LayoutX']


In [30]:
unique_packaging_quality = density_reports['PackagingQuality'].unique()
print("Unique values of PackagingQuality:", unique_packaging_quality)

Unique values of PackagingQuality: ['Good' 'Bad' 'GOOD' 'Uncertain' 'bad']


The `PackagingQuality` column, our **target variable**, contains inconsistencies in value naming (e.g., variations in capitalization or spelling). Standardizing this column is especially critical, as it directly affects model training and label accuracy. The following code will ensure that all values are consistently labeled (e.g., unified as `"Good"` and `"Bad"`), enabling reliable classification and evaluation.


In [31]:
# Count unique values for the PackagingQuality column in density_reports
packaging_quality_counts = density_reports['PackagingQuality'].value_counts(dropna=False)
print("Counts for each unique value in PackagingQuality:")
print(packaging_quality_counts)


Counts for each unique value in PackagingQuality:
PackagingQuality
Good         380520
Bad           92899
GOOD           1835
bad            1801
Uncertain      1791
Name: count, dtype: int64


In [32]:
# Step 1: Convert to lowercase and strip spaces
density_reports['PackagingQuality'] = density_reports['PackagingQuality'].astype(str).str.strip().str.lower()

# Step 2: Map to standardized values
quality_mapping = {
    'good': 'Good',
    'bad': 'Bad',
    'uncertain': 'Uncertain'
}

density_reports['PackagingQuality'] = density_reports['PackagingQuality'].replace(quality_mapping)

# Step 3: Check cleaned unique values
print(sorted(density_reports['PackagingQuality'].unique()))


['Bad', 'Good', 'Uncertain']


In [33]:
print("density_reports shape:", density_reports.shape)

density_reports shape: (478846, 11)


In [34]:
total_expected = 500000
actual_count = density_reports.shape[0]
difference = total_expected - actual_count
ratio = actual_count / total_expected

print(f"Difference: {difference}")
print(f"Ratio: {ratio:.4f}")

Difference: 21154
Ratio: 0.9577


After applying the cleaning steps,including filtering invalid values, removing rows with missing or inconsistent entries, and standardizing key columns, the `DensityReports` dataset was reduced to **478,846 records**, which is **21,154 fewer** than the original. This represents a reduction of approximately **4.23%** of the total data, ensuring a cleaner and more reliable foundation for downstream analysis.


### Cleaning Product Attributes

Summary of Data Cleaning for `ProductAttributes`

No cleaning was required for this dataset. All integrity checks were passed, and the data is consistent across key fields such as `ProductReference`, `ProductName`, `GarmentType`, `Material`, and `Size`.


In [35]:
print("product_attributes columns:", product_attributes.columns.tolist())
print("product_attributes shape:", product_attributes.shape)

product_attributes columns: ['ProductReference', 'ProductName', 'GarmentType', 'Material', 'Size', 'Collection', 'Weight']
product_attributes shape: (10000, 7)


In [36]:
unique_product_names = product_attributes['ProductName'].unique()
print("Unique values of ProductName:", unique_product_names)

Unique values of ProductName: ['Jacket Cotton L' 'Shorts Cotton S' 'Sweater Cotton M'
 'Skirt Polyester L' 'Shirt Polyester M' 'Shirt Silk L' 'Shirt Cotton XL'
 'T-Shirt Polyester S' 'Skirt Linen L' 'Coat Linen S' 'Shirt Silk M'
 'Shorts Wool XS' 'T-Shirt Silk S' 'Pants Cotton M' 'Shirt Cotton L'
 'Pants Cotton L' 'Dress Cotton XL' 'Jacket Cotton M' 'Pants Cotton S'
 'Suit Cotton M' 'Shirt Cotton M' 'Pants Silk M' 'Dress Wool M'
 'T-Shirt Cotton M' 'Shirt Silk S' 'Dress Silk XS' 'Skirt Wool S'
 'Shirt Wool S' 'Skirt Cotton L' 'Shirt Denim S' 'Shorts Silk M'
 'Shorts Wool S' 'T-Shirt Cotton L' 'Shirt Cotton S' 'Coat Polyester L'
 'Jacket Cotton XS' 'Dress Cotton L' 'Blouse Polyester M' 'Pants Linen S'
 'Suit Polyester L' 'Dress Cotton S' 'Skirt Linen M' 'Shirt Denim XL'
 'Shorts Linen XS' 'T-Shirt Polyester L' 'Shorts Polyester XL'
 'Shirt Polyester S' 'Shirt Linen S' 'Shirt Polyester XL'
 'Pants Cotton XL' 'Skirt Wool M' 'Shirt Wool M' 'T-Shirt Linen L'
 'Hoodie Silk M' 'T-Shirt Denim 

In [37]:
unique_sizes = product_attributes['Size'].unique()
print("Unique values of Size:", unique_sizes)

Unique values of Size: ['L' 'S' 'M' 'XL' 'XS']


In [38]:
unique_garment_types_attr = product_attributes['GarmentType'].unique()
unique_materials_attr = product_attributes['Material'].unique()
print("Unique GarmentType values in product_attributes:", unique_garment_types_attr)
print("Unique Material values in product_attributes:", unique_materials_attr)

Unique GarmentType values in product_attributes: ['Jacket' 'Shorts' 'Sweater' 'Skirt' 'Shirt' 'T-Shirt' 'Coat' 'Pants'
 'Dress' 'Suit' 'Blouse' 'Hoodie']
Unique Material values in product_attributes: ['Cotton' 'Polyester' 'Silk' 'Linen' 'Wool' 'Denim']


This block verifies that the `ProductName` column correctly follows the expected format: `"GarmentType Material Size"`. It identifies and displays rows where the actual name does not match the constructed format, helping to catch formatting errors or data entry issues.


In [39]:
# Build expected format string
expected_names = product_attributes.apply(
    lambda row: f"{row['GarmentType']} {row['Material']} {row['Size']}",
    axis=1
)

# Compare to actual ProductName
mismatch_mask = product_attributes['ProductName'] != expected_names
mismatches = product_attributes[mismatch_mask]

# Output
print(f"Strict mismatches (wrong format): {mismatches.shape[0]}")
print(mismatches[['ProductName', 'GarmentType', 'Material', 'Size']])


Strict mismatches (wrong format): 0
Empty DataFrame
Columns: [ProductName, GarmentType, Material, Size]
Index: []


In [40]:
unique_collections = product_attributes['Collection'].unique()
print("Unique values of Collection:", unique_collections)

Unique values of Collection: ['Summer' 'Spring' 'Winter' 'Autumn']


In [41]:
print("Unique values of Weight in product_attributes:", np.sort(product_attributes['Weight'].unique()))

Unique values of Weight in product_attributes: [0.08 0.09 0.1  0.11 0.12 0.13 0.14 0.15 0.16 0.17 0.18 0.19 0.2  0.21
 0.22 0.23 0.24 0.25 0.26 0.27 0.28 0.29 0.3  0.31 0.32 0.33 0.34 0.35
 0.36 0.37 0.38 0.39 0.4  0.41 0.42 0.43 0.44 0.45 0.46 0.47 0.48 0.49
 0.5  0.51 0.52 0.53 0.54 0.55 0.56 0.57 0.58 0.59 0.6  0.61 0.62 0.63
 0.64 0.65 0.66 0.67 0.68 0.69 0.7  0.71 0.72 0.73 0.74 0.75 0.76 0.77
 0.78 0.79 0.8  0.81 0.82 0.83 0.84 0.85 0.86 0.87 0.88 0.89 0.9  0.91
 0.92 0.93 0.94 0.95 0.96 0.97 0.98 0.99 1.   1.01 1.02 1.03 1.04 1.05
 1.06 1.07 1.08 1.09 1.1  1.11 1.12 1.13 1.14 1.15 1.16 1.17 1.18 1.19
 1.2  1.21 1.22 1.23 1.24 1.25 1.26 1.27 1.28 1.29 1.3  1.31 1.32 1.33
 1.34 1.35 1.36 1.37 1.38 1.39 1.4  1.41 1.42 1.43 1.44 1.45 1.46 1.47
 1.48 1.49 1.5  1.51 1.52 1.53 1.54 1.55 1.56 1.57 1.58 1.59 1.6  1.61
 1.62 1.63 1.64 1.65 1.66 1.67 1.68 1.69 1.7  1.71 1.72 1.73 1.74 1.76
 1.77 1.79 1.8  1.81 1.82 1.83 1.85 1.86 1.88 1.89 1.91 1.92 1.93 1.95
 1.96 1.99 2.   2.01 2.02 2.03

In [42]:
# Check for null values in product_attributes
null_counts = product_attributes.isna().sum()
print("NaN values per column in product_attributes:")
print(null_counts)

NaN values per column in product_attributes:
ProductReference    0
ProductName         0
GarmentType         0
Material            0
Size                0
Collection          0
Weight              0
dtype: int64


### Cleaning Supplier ScoreCard

Summary of Data Cleaning for `SupplierScorecard`

- Column names were standardized by removing spaces and special characters to ensure compatibility with queries and downstream processing.
- `SupplierName` values were cleaned by stripping whitespace, converting to lowercase, and applying a mapping to correct naming inconsistencies.
- The dataset is now structurally consistent and ready for integration and analysis.


In [43]:
supplier_scorecard = pd.read_excel("data/raw/SupplierScorecard.xlsx")
print("supplier_scorecard columns:", supplier_scorecard.columns.tolist())
print("supplier_scorecard shape:", supplier_scorecard.shape)


supplier_scorecard columns: ['SupplierName', 'Month', 'PackagesHandled', 'BadPackagingRate (%)', 'TotalIncidents', 'AverageCostPerIncident (€)', 'OnTimeDeliveryRate (%)', 'AnomaliesDetected']
supplier_scorecard shape: (252, 8)


 Standardize column names by removing spaces and special characters to avoid querying issues


In [44]:
# Remove spaces and special characters from column names in supplier_scorecard
supplier_scorecard = supplier_scorecard.rename(columns={
    'BadPackagingRate (%)': 'BadPackagingRatePct',
    'AverageCostPerIncident (€)': 'AverageCostPerIncidentEUR',
    'OnTimeDeliveryRate (%)': 'OnTimeDeliveryRatePct'
})

# Also remove any remaining spaces in column names
supplier_scorecard.columns = [col.replace(' ', '') for col in supplier_scorecard.columns]

print(supplier_scorecard.columns.tolist())

['SupplierName', 'Month', 'PackagesHandled', 'BadPackagingRatePct', 'TotalIncidents', 'AverageCostPerIncidentEUR', 'OnTimeDeliveryRatePct', 'AnomaliesDetected']


In [45]:
print("Unique values of SupplierName in supplier_scorecard:", supplier_scorecard['SupplierName'].unique())
print("Unique values of SupplierName in density_reports:", density_reports['SupplierName'].unique())

Unique values of SupplierName in supplier_scorecard: ['SupplierA' 'SupplierC' 'SupplierD' 'SupplierB' 'supplierA' 'SupplierF'
 'SupplierE' 'supplierh' 'SupplierH' 'SuppB' 'SupplierG' 'SupllierC'
 'SPLF' 'SuplA']
Unique values of SupplierName in density_reports: ['SupplierA' 'SupplierC' 'SupplierD' 'SupplierB' 'SupplierF' 'SupplierE'
 'SupplierH' 'SupplierG']


As the output above displays, several suppliers appear with inconsistent or misspelled names across the datasets, often due to variations in spacing, capitalization, or typographical errors. To ensure reliable merging and analysis based on `SupplierName`, the following code standardizes these entries by converting all names a consistent, unified format.


In [46]:
# Step 1: Normalize casing and strip
supplier_scorecard['SupplierName'] = supplier_scorecard['SupplierName'].astype(str).str.strip().str.lower()

# Step 2: Updated mapping
supplier_mapping = {
    'suppliera': 'SupplierA',
    'supplierb': 'SupplierB',
    'supplierc': 'SupplierC',
    'supplierd': 'SupplierD',
    'suppliere': 'SupplierE',
    'supplierf': 'SupplierF',
    'supplierg': 'SupplierG',
    'supplierh': 'SupplierH',
    'suppb': 'SupplierB',
    'supla': 'SupplierA',        
    'supllierc': 'SupplierC',
    'splf': 'SupplierF'
}

# Step 3: Replace
supplier_scorecard['SupplierName'] = supplier_scorecard['SupplierName'].replace(supplier_mapping)

# Step 4: Check final cleaned values
print(sorted(supplier_scorecard['SupplierName'].unique()))


['SupplierA', 'SupplierB', 'SupplierC', 'SupplierD', 'SupplierE', 'SupplierF', 'SupplierG', 'SupplierH']


In [47]:
supplier_scorecard['Month'] = pd.to_datetime(supplier_scorecard['Month'], format='%Y-%m')

In [48]:
for col in supplier_scorecard.columns:
    if col not in ['SupplierName', 'Month']:
        unique_vals = supplier_scorecard[col].unique()
        print(f"Unique values for {col}: {unique_vals}")

Unique values for PackagesHandled: [7841 7196 7842 7587 8010 7516 7924 8019 7616 7726 7487 7877 7878 7376
 7828 7578 7796 7510 4336 3771 4208 3938 4262 4185 4354 4132 4107 4141
 4111 4222 4154 3877 4190 4134 4242 4126 3038 2788 3142 2854 3100 2987
 3004 2984 2953 2860 3003 3019 2945 3024 2859 2957 2946 6336 5701 6108
 6040 6411 6045 6350 6298 6130 6167 5978 6267 6281 5826 6391 5968 6283
 6143  102   75  100  101   84  111  108  103   88   91   73   86  110
   93  117 1932 1663 1823 1828 1901 1766 1855 1867 1787 1885 1791 1863
 1888 1723 1806 1812 1861 1794 2306 2077 2329 2170 2242 2091 2356 2194
 2257 2300 2303 2377 2350 2211 2323 2221 2315 2240   95   92   97   94
   85  104   87   90  781  687  833  773  793  746  724  799  771  851
  735  713  789  695  756  759   74   76   80  114   89   98   83 1416
 1343 1469 1453 1363 1354 1512 1426 1376 1485 1358 1449 1468 1435 1425
 1350 1429 1399  107   99  109   78   82  105   66   69  116   79   81]
Unique values for BadPackagingRatePct: [ 

In [49]:
# Updated aggregation using corrected column names
def weighted_avg(df, value_col, weight_col):
    return (df[value_col] * df[weight_col]).sum() / df[weight_col].sum()

# Group and aggregate with appropriate logic
supplier_scorecard = (
    supplier_scorecard
    .groupby(['SupplierName', 'Month'], as_index=False)
    .apply(lambda group: pd.Series({
        'PackagesHandled': group['PackagesHandled'].sum(),
        'TotalIncidents': group['TotalIncidents'].sum(),
        'AnomaliesDetected': group['AnomaliesDetected'].sum(),
        'BadPackagingRatePct': weighted_avg(group, 'BadPackagingRatePct', 'PackagesHandled'),
        'OnTimeDeliveryRatePct': weighted_avg(group, 'OnTimeDeliveryRatePct', 'PackagesHandled'),
        'AverageCostPerIncidentEUR': weighted_avg(group, 'AverageCostPerIncidentEUR', 'TotalIncidents') if group['TotalIncidents'].sum() > 0 else group['AverageCostPerIncidentEUR'].mean()
    }))
    .reset_index()
)

print(supplier_scorecard.head())

   index SupplierName      Month  PackagesHandled  TotalIncidents  \
0      0    SupplierA 2023-01-01           8019.0           137.0   
1      1    SupplierA 2023-02-01           7356.0           160.0   
2      2    SupplierA 2023-03-01           8045.0           170.0   
3      3    SupplierA 2023-04-01           7778.0           164.0   
4      4    SupplierA 2023-05-01           8209.0           175.0   

   AnomaliesDetected  BadPackagingRatePct  OnTimeDeliveryRatePct  \
0               25.0             8.658785              85.881892   
1               18.0             8.018635              87.971383   
2               22.0             8.199500              84.750558   
3               19.0             7.999447              91.290513   
4               20.0             8.056751              96.461146   

   AverageCostPerIncidentEUR  
0                 537.361971  
1                 565.884000  
2                 548.924294  
3                 594.712866  
4                 611

C:\Users\Paulm\AppData\Local\Temp\ipykernel_13920\421388214.py:9: DeprecationWarning:

DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.



### Cleaning Historical Incidents


Summary of Data Cleaning for `HistoricalIncidents`

- Unmatched `ProductReference` values (e.g., `PRD00` to `PRD09`) were identified and removed due to inconsistent or incomplete product information.
- `ProductReference` values ending in "X" were standardized by removing the "X" to align with their base codes.
- `SupplierName` values were cleaned by stripping whitespace, normalizing casing, and applying a mapping to correct known variations and misspellings.
- The dataset is now consistent and ready for integration with the other sources.


In [50]:
print("historical_incidents columns:", historical_incidents.columns.tolist())
print("historical_incidents shape:", historical_incidents.shape)

historical_incidents columns: ['ProductReference', 'SupplierName', 'DateOfIncident', 'IssueDescription', 'ResolutionStatus', 'CostImpact (€)']
historical_incidents shape: (18000, 6)


 Standardize column names by removing spaces and special characters to avoid querying issues


In [51]:
# Rename 'CostImpact (€)' column to remove spaces
historical_incidents = historical_incidents.rename(columns={'CostImpact (€)': 'CostImpactEUR'})


This step verifies data consistency by checking whether all `ProductReference` values in the `HistoricalIncidents` dataset are present in the `ProductAttributes` dataset. Since `ProductReference` is a key linking field across datasets, any missing values could indicate data entry issues, obsolete product codes, or taxonomy mismatches. The code below identifies and counts any such unmatched references to assess whether they should be excluded or reconciled

In [52]:
# Find unique ProductReference values in each dataframe
density_refs = set(historical_incidents['ProductReference'].unique())
attributes_refs = set(product_attributes['ProductReference'].unique())

# Find ProductReference values in historical_incidents not present in product_attributes
missing_refs = density_refs - attributes_refs

# Filter only rows with missing ProductReference values once
if missing_refs:
    missing_df = historical_incidents[historical_incidents['ProductReference'].isin(missing_refs)]
    counts = missing_df['ProductReference'].value_counts()

    print("ProductReference values in historical_incidents not present in product_attributes:")
    for ref, count in counts.items():
        print(f"{ref}: {count} rows")
    print(f"\nTotal missing ProductReference values: {len(missing_refs)}")
else:
    print("All ProductReference values in historical_incidents are present in product_attributes.")

ProductReference values in historical_incidents not present in product_attributes:
PRD06: 37 rows
PRD03: 33 rows
PRD00: 32 rows
PRD01: 31 rows
PRD07: 31 rows
PRD08: 31 rows
PRD05: 28 rows
PRD04: 27 rows
PRD09: 27 rows
PRD02: 24 rows
PRD03714X: 2 rows
PRD09639X: 2 rows
PRD05614X: 2 rows
PRD00146X: 2 rows
PRD03465X: 2 rows
PRD01393X: 1 rows
PRD05122X: 1 rows
PRD02845X: 1 rows
PRD02235X: 1 rows
PRD03852X: 1 rows
PRD06610X: 1 rows
PRD06388X: 1 rows
PRD01844X: 1 rows
PRD05441X: 1 rows
PRD02349X: 1 rows
PRD04922X: 1 rows
PRD01437X: 1 rows
PRD02985X: 1 rows
PRD04083X: 1 rows
PRD00209X: 1 rows
PRD03783X: 1 rows
PRD01019X: 1 rows
PRD08524X: 1 rows
PRD07773X: 1 rows
PRD03942X: 1 rows
PRD01308X: 1 rows
PRD03446X: 1 rows
PRD01887X: 1 rows
PRD05375X: 1 rows
PRD08658X: 1 rows
PRD09897X: 1 rows
PRD02828X: 1 rows
PRD00517X: 1 rows
PRD05578X: 1 rows
PRD09202X: 1 rows
PRD09084X: 1 rows
PRD07652X: 1 rows
PRD07337X: 1 rows
PRD00803X: 1 rows
PRD07694X: 1 rows
PRD02582X: 1 rows
PRD02172X: 1 rows
PRD00266X: 

As with previous datasets, we observe that certain `ProductReference` values (e.g., `PRD00` to `PRD09`) are not present in `ProductAttributes` and display inconsistent product information. These entries will be dropped. Additionally, references ending in "X" are standardized by removing the "X", as they refer to the same underlying products as their base codes.


In [53]:
target_refs = ['PRD06', 'PRD00', 'PRD01', 'PRD05', 'PRD03', 
               'PRD02', 'PRD07', 'PRD08', 'PRD09', 'PRD04']

historical_incidents = historical_incidents[~historical_incidents['ProductReference'].isin(target_refs)].reset_index(drop=True)
historical_incidents['ProductReference'] = historical_incidents['ProductReference'].str.replace('X', '', regex=False)

In [54]:
print("Unique values of SupplierName in historical_incidents:", historical_incidents['SupplierName'].unique())


Unique values of SupplierName in historical_incidents: ['SupplierC' 'SupplierA' 'SupplierE' 'SupplierB' 'SupplierF' 'SupplierD'
 'SupllierC' 'SupplierH' 'SPLF' 'supplierh' 'SupplierG' 'supplierA'
 'SuppB' 'SuplA']


To ensure consistency across datasets, this step normalizes `SupplierName` values by converting them to lowercase, stripping whitespace, and applying a mapping to correct common misspellings or formatting variations. This standardization is essential for accurate merging and analysis involving supplier-related performance and incident history.


In [55]:
# Step 1: Normalize to lowercase and strip
historical_incidents['SupplierName'] = historical_incidents['SupplierName'].astype(str).str.strip().str.lower()

# Step 2: Mapping of incorrect forms to standardized names
supplier_mapping = {
    'suppliera': 'SupplierA',
    'supplierb': 'SupplierB',
    'supplierc': 'SupplierC',
    'supplierd': 'SupplierD',
    'suppliere': 'SupplierE',
    'supplierf': 'SupplierF',
    'supplierg': 'SupplierG',
    'supplierh': 'SupplierH',
    'suppb': 'SupplierB',
    'supla': 'SupplierA',
    'supllierc': 'SupplierC',
    'splf': 'SupplierF'
}

# Step 3: Apply mapping
historical_incidents['SupplierName'] = historical_incidents['SupplierName'].replace(supplier_mapping)

# Step 4: Final check
print(sorted(historical_incidents['SupplierName'].unique()))


['SupplierA', 'SupplierB', 'SupplierC', 'SupplierD', 'SupplierE', 'SupplierF', 'SupplierG', 'SupplierH']


In [56]:
historical_incidents['DateOfIncident'] = pd.to_datetime(historical_incidents['DateOfIncident'])

In [57]:
unique_issue_descriptions = historical_incidents['IssueDescription'].unique()
print("Unique values of IssueDescription in historical_incidents:", unique_issue_descriptions)

Unique values of IssueDescription in historical_incidents: ['Other' 'Packaging Damage' 'Missing Items' 'Incorrect Folding'
 'Labeling Error' 'Product Wrinkled' 'Transportation Damage']


In [58]:
unique_resolution_status = historical_incidents['ResolutionStatus'].unique()
print("Unique values of ResolutionStatus in historical_incidents:", unique_resolution_status)

Unique values of ResolutionStatus in historical_incidents: ['Resolved' 'In Progress' 'Not Resolved']


In [59]:
unique_cost_impact = historical_incidents['CostImpactEUR'].unique()
print("Unique values of CostImpact (€):", np.sort(unique_cost_impact))

Unique values of CostImpact (€): [  50.     51.     52.   ... 2497.5  2498.75 2500.  ]


### Processed Data Download

In [61]:
# Save the latest cleaned dataframes to CSV in data/processed
density_reports.to_csv("data/processed/density_reports.csv", index=False)
product_attributes.to_csv("data/processed/product_attributes.csv", index=False)
supplier_scorecard.to_csv("data/processed/supplier_scorecard.csv", index=False)
historical_incidents.to_csv("data/processed/historical_incidents.csv", index=False)